In [1]:
import os
os.environ["CALITP_BQ_MAX_BYTES"] = str(1_000_000_000_000) ## 1TB?
import sys

from siuba import *
import pandas as pd
import geopandas as gpd
import gcsfs
import datetime as dt
import time
import shapely

from rt_analysis import rt_parser
from rt_analysis import rt_filter_map_plot

import shared_utils
from calitp_data_analysis.tables import tbls

/opt/conda/lib/python3.9/site-packages/geopandas/_compat.py:123: UserWarning: The Shapely GEOS version (3.10.3-CAPI-1.16.1) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(


# Migrate existing rt_analysis to use the v2 warehouse 

* mostly just changing queries around

In [2]:
# date for v2 testing
analysis_date = dt.date(2023, 3, 15)

## Does it work?

In [ ]:
rt_parser.OperatorDayAnalysis?

In [ ]:
analysis_date

In [ ]:
from tqdm.notebook import tqdm

In [ ]:
pbar = tqdm()

In [ ]:
%%capture --no-stdout
rt_day = rt_parser.OperatorDayAnalysis(183, analysis_date, pbar)

In [ ]:
rt_day.export_views_gcs()

In [ ]:
rt_day = rt_filter_map_plot.RtFilterMapper(rt_day.rt_trips, rt_day.stop_delay_view, rt_day.shapes, pbar)

In [ ]:
rt_day.set_filter(start_time = '06:00', end_time = '09:00')

In [ ]:
m = rt_day.segment_speed_map()

In [ ]:
m

## Before Merging

* use new folder, restore caching, move to rt_utils
    * testing caching; move pending
* backwards compatibility -- RtFilterMapper shall accept and use v1 for pre-2023 dates (done)
* message change with Chaithra, pre-stage 2 weeks for SFMTA, AC Transit, SDMTS using v1 around Oct date's she's already using
    * example notebook (or just point to relevant tutorial)
    * staged Oct 9 thru 15
    * note that she's welcome to rerun recent dates with v2
* _some time later_
    * advocate to delete v1 tables
    * remove v1 cached data

In [ ]:
# rt_day.export_views_gcs()

## Backwards compatibility

In [ ]:
v1_date = dt.date(2022, 10, 9)

In [ ]:
rt_day = rt_filter_map_plot.from_gcs(4, v1_date, pbar)

In [ ]:
rt_day.set_filter(start_time = '06:00', end_time = '09:00')

In [ ]:
rt_day.segment_speed_map()

In [37]:
rt_day = rt_filter_map_plot.from_gcs(277, analysis_date, pbar)

found shapes parquet at gs://calitp-analytics-data/data-analyses/rt_delay/v2_cached_views/shapes_277_2023-03-15.parquet


In [38]:
rt_day.set_filter(start_time = '06:00', end_time = '09:00')

In [39]:
rt_day.segment_speed_map()

stop_speeds shape: (0, 12), shape_id: 115_2_79
stop speeds gdf is empty!
stop_speeds shape: (0, 12), shape_id: 905_2_90
stop speeds gdf is empty!


/opt/conda/lib/python3.9/site-packages/shapely/ops.py:639: ShapelyDeprecationWarning: GeometryTypeError will derive from ShapelyError and not TypeError or ValueError in Shapely 2.0.
/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:406: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

/home/jovyan/data-analyses/rt_delay/rt_analysis/rt_filter_map_plot.py:406: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.



In [ ]:
## TODO print warning

## debug queries

## What's up with SacRT??

In [3]:
rt_parser.OperatorDayAnalysis?

Init signature: rt_parser.OperatorDayAnalysis(itp_id, analysis_date, pbar=None)
Docstring:     
New top-level class for rt delay/speed analysis of a single operator on a single day
    
File:           ~/data-analyses/rt_delay/rt_analysis/rt_parser.py
Type:           type
Subclasses:     

In [ ]:
ix_df = shared_utils.rt_utils.get_ix_df(273, analysis_date)

In [15]:
# ix_df

In [12]:
feed_key_list = list(ix_df.feed_key.unique())

In [11]:
# shared_utils.rt_utils.get_shapes(ix_df)

/opt/conda/lib/python3.9/site-packages/sqlalchemy_bigquery/_types.py:101: SAWarning: Did not recognize type 'GEOGRAPHY' of column 'pt_array'


AssertionError: routelines must not be empty

In [17]:
feed_key_list

['6a2e7a3646843b2bf2430bef13c3142a']

In [24]:
daily_service = (tbls.mart_gtfs.fct_daily_feed_scheduled_service_summary()
# >> select(_.schedule_gtfs_dataset_key == _.gtfs_dataset_key,
#          _.feed_key, _.activity_date)
# >> filter(_.feed_key.isin(feed_key_list))
>> filter(_.gtfs_dataset_key == 'ae1c2f25d0d162bf2a0e90527a8eecec')
            )


In [27]:
## classic SacRT -- uploaded a new feed but no service 'til April 2...

In [26]:
daily_service >> collect() >> arrange(_.activity_date)

activity_date                          feed_key  \
24    2023-01-19  008d5112a7e531d0562d26e34d77869d   
16    2023-01-20  008d5112a7e531d0562d26e34d77869d   
42    2023-01-21  008d5112a7e531d0562d26e34d77869d   
49    2023-01-22  008d5112a7e531d0562d26e34d77869d   
12    2023-01-23  008d5112a7e531d0562d26e34d77869d   
32    2023-01-24  008d5112a7e531d0562d26e34d77869d   
35    2023-01-25  008d5112a7e531d0562d26e34d77869d   
33    2023-01-26  008d5112a7e531d0562d26e34d77869d   
25    2023-01-27  008d5112a7e531d0562d26e34d77869d   
48    2023-01-28  008d5112a7e531d0562d26e34d77869d   
52    2023-01-29  008d5112a7e531d0562d26e34d77869d   
19    2023-01-30  008d5112a7e531d0562d26e34d77869d   
18    2023-01-31  008d5112a7e531d0562d26e34d77869d   
29    2023-02-01  008d5112a7e531d0562d26e34d77869d   
30    2023-02-02  008d5112a7e531d0562d26e34d77869d   
34    2023-02-03  008d5112a7e531d0562d26e34d77869d   
45    2023-02-04  008d5112a7e531d0562d26e34d77869d   
50    2023-02-05  008d5112a7e531d0562d26e34d77869d   
20    2023-02-06  008d5112a7e531d0562d26e34d77869d   
39    2023-02-07  008d5112a7e531d0562d26e34d77869d   
28    2023-02-08  008d5112a7e531d0562d26e34d77869d   
37    2023-02-09  008d5112a7e531d0562d26e34d77869d   
14    2023-02-10  008d5112a7e531d0562d26e34d77869d   
43    2023-02-11  008d5112a7e531d0562d26e34d77869d   
53    2023-02-12  008d5112a7e531d0562d26e34d77869d   
31    2023-02-13  008d5112a7e531d0562d26e34d77869d   
17    2023-02-14  008d5112a7e531d0562d26e34d77869d   
22    2023-02-15  008d5112a7e531d0562d26e34d77869d   
23    2023-02-16  008d5112a7e531d0562d26e34d77869d   
38    2023-02-17  008d5112a7e531d0562d26e34d77869d   
47    2023-02-18  008d5112a7e531d0562d26e34d77869d   
55    2023-02-19  008d5112a7e531d0562d26e34d77869d   
26    2023-02-20  008d5112a7e531d0562d26e34d77869d   
8     2023-02-21  008d5112a7e531d0562d26e34d77869d   
36    2023-02-22  008d5112a7e531d0562d26e34d77869d   
9     2023-02-23  008d5112a7e531d0562d26e34d77869d   
10    2023-02-24  008d5112a7e531d0562d26e34d77869d   
46    2023-02-25  008d5112a7e531d0562d26e34d77869d   
54    2023-02-26  008d5112a7e531d0562d26e34d77869d   
11    2023-02-27  008d5112a7e531d0562d26e34d77869d   
13    2023-02-28  008d5112a7e531d0562d26e34d77869d   
27    2023-03-01  008d5112a7e531d0562d26e34d77869d   
40    2023-03-02  008d5112a7e531d0562d26e34d77869d   
41    2023-03-03  008d5112a7e531d0562d26e34d77869d   
44    2023-03-04  008d5112a7e531d0562d26e34d77869d   
51    2023-03-05  008d5112a7e531d0562d26e34d77869d   
21    2023-03-06  008d5112a7e531d0562d26e34d77869d   
15    2023-03-07  008d5112a7e531d0562d26e34d77869d   
0     2023-03-08  509bab37af6fb54de2d7bd21ad04fa39   
3     2023-03-09  509bab37af6fb54de2d7bd21ad04fa39   
1     2023-03-10  509bab37af6fb54de2d7bd21ad04fa39   
2     2023-03-11  6a2e7a3646843b2bf2430bef13c3142a   
6     2023-03-12  6a2e7a3646843b2bf2430bef13c3142a   
7     2023-03-13  6a2e7a3646843b2bf2430bef13c3142a   
5     2023-03-14  6a2e7a3646843b2bf2430bef13c3142a   
4     2023-03-15  6a2e7a3646843b2bf2430bef13c3142a   

                    gtfs_dataset_key  ttl_service_hours  n_trips  \
24  ae1c2f25d0d162bf2a0e90527a8eecec        1698.983333     2460   
16  ae1c2f25d0d162bf2a0e90527a8eecec        1698.983333     2460   
42  ae1c2f25d0d162bf2a0e90527a8eecec        1078.766667     1414   
49  ae1c2f25d0d162bf2a0e90527a8eecec         820.000000     1120   
12  ae1c2f25d0d162bf2a0e90527a8eecec        1698.983333     2460   
32  ae1c2f25d0d162bf2a0e90527a8eecec        1698.983333     2460   
35  ae1c2f25d0d162bf2a0e90527a8eecec        1698.983333     2460   
33  ae1c2f25d0d162bf2a0e90527a8eecec        1698.983333     2460   
25  ae1c2f25d0d162bf2a0e90527a8eecec        1698.983333     2460   
48  ae1c2f25d0d162bf2a0e90527a8eecec        1078.766667     1414   
52  ae1c2f25d0d162bf2a0e90527a8eecec         820.000000     1120   
19  ae1c2f25d0d162bf2a0e90527a8eecec        1698.983333     2460   
18  ae1c2f25d0d162bf2a0e90527a8eecec    